In [1]:
import emat
emat.versions()

emat 0.6.4, plotly 5.24.1


# Interactive Explorer

TMIP-EMAT includes an interactive visualizer, inspired by a 
[similar tool](https://htmlpreview.github.io/?https://github.com/VisionEval/VisionEval/blob/master/sources/VEScenarioViewer/verpat.html) 
provided with the [VisionEval](https://visioneval.org) package.
To demonstrate the interactive visualizer, we will use the Road Test example model.
First, we need to develop and run a design of experiments to have some
data to explore.  We'll run 5,000 experiments to get a good size sample of 
data points to visualize.

In [2]:
import emat.examples
scope, db, model = emat.examples.road_test()
design = model.design_experiments(n_samples=5000)
results = model.run_experiments(design)

One feature of the visualizer is the ability to display not only a number of results,
but also to contrast those results against a given "reference" model that represents
a more traditional single-point forecast of inputs and results.  We'll prepare a
reference point here using the `run_reference_experiment` method of the `CoreModel`
class, which reads the input parameter defaults (as defined in the scope),
and returns both inputs and outputs in a DataFrame (essentially, an experimental
design with only a single experiment), suitable for use as the reference point marker in our
visualizations.

In [3]:
refpoint = model.run_reference_experiment()

The interactive visualizer class can be imported from the `emat.analysis` package.
To use it, we create an `Visualizer` instance, giving a scope and a set of 
experimental results, as well as the reference point.

In [4]:
from emat.analysis import Visualizer

In [5]:
viz = Visualizer(scope=scope, data=results, reference_point=refpoint)

## Single Dimension Figures

To build a complete interactive workspace similar to that provided by VisionEval, we
can use the `complete` method of the `Visualizer` instance we created above. This will
create a set of histograms illustrating the data in the results computed above. There
is one histogram for each policy lever, exogenous uncertainty, and performance measure.

A range of data in each histogram can be selected by dragging horizonatally across the 
figure. For continuous parameters (i.e. float or integer valued parameters) you can 
select a single contiguous range by dragging across that range, and deselect by double 
clicking on the figure (or by selecting the entire possible range).  For discrete 
parameters (i.e. boolean or categorical parameters, identifiable by the larger gaps
between the bars in the figure) dragging across the center of any bar toggles whether
that bar is selected or not.  This allows non-contiguous selections in categories that
have 3 or more possible values.  Like the other figures, any selection can be cleared 
by double-clicking.

Selections can be made simultaneously over any combination of uncertainties, policy levers,
and performance measures.  The combination of controls offered can 
be used interactively to select and highlight only a subset of the experiments in
the complete data set.  By manipulating these controls, users can explore the 
interaction across various inputs and outputs.

![Selecting from histograms](interactive-gifs/select-from-histograms-.gif)

In [6]:
viz.complete()

OVERLOAD BINS 20 4 36
OVERLOAD BINS 20 4 71


It is also possible to display just a small subset of the figures of this interactive viewer.
This could be convenient, for example, if there are a very large number of performance measures.

In [7]:
viz.selectors(['input_flow', 'expand_capacity', 'net_benefits'])

OVERLOAD BINS 20 4 71


Box(children=(VBox(children=(FigureWidget({
    'data': [{'hoverinfo': 'skip',
              'marker': {'color…

In [8]:
box = emat.Box("Passable", scope=scope)
box.set_upper_bound('cost_of_capacity_expansion', 400)
box.set_lower_bound('time_savings', 5)
box.remove_from_allowed_set('debt_type', 'GO Bond')
viz.add_box(box)

Alternatively, a new box can be created and added to the Visualier
with a single :meth:`Visualizer.new_box` command, which
passes most keyword arguments through to the :class:`emat.Box` constuctor.

In [9]:
viz.new_box('Profitable', lower_bounds={'net_benefits':0});

Each of these new boxes is added to the `Visualizer` seperately. You can
switch between different active boxes using the dropdown selector at the top 
of the `complete` interface -- this same selector is available within the
smaller `status` widget:

In [10]:
viz.status()

You can also programatically find and change the active box from Python:

In [11]:
viz.active_selection_name()

'Profitable'

In [12]:
viz.set_active_selection_name("Passable")
viz.active_selection_name()

'Passable'

When interactively changing bounds by dragging on figures, the currently 
"active" box is modified with the revised bounds.  The entire set of
bounds can be cleared at once with the `clear_box` method, which by default 
clears the settings on the active box selection; give a name to clear the 
settings from a different box selection.

In [13]:
viz.clear_box()

If instead we want to manipulate an existing box selection, we can access the Box object, 
manipulate it (e.g. by using `remove_from_allowed_set` or `add_to_allowed_set`), 
and write it back into the Visualizer.

In [14]:
box = viz['Profitable']
box.remove_from_allowed_set('debt_type', 'Rev Bond')
viz['Profitable'] = box

## Two Dimension Figures

The `Visualizer` object can also create an interactive two-dimensional scatter plot,
using the `two_way` method. This method allows the user to specify the variables
for both the `x` and `y` axis, and either can be any policy lever, exogenous 
uncertainty, or performance measure.  These dimensions can be changed interactively
later as well.  The resulting scatter plot is linked to the same selection of
experiments in the interactive one-dimensional figures shown above, and by default
the same experiments are highlighted in the same color scheme in all of these related
figures.

In [15]:
viz.two_way(x='expand_capacity', y='time_savings')

TwoWayFigure(children=(FigureWidget({
    'data': [{'hovertemplate': ('%{xaxis.title.text}: %{x}<br>%' ... 'tr…

One useful feature of the `two_way` is the ability to manually "lasso" a selection of 
data points. This lasso selection does *not* need to be anything like a rectangular 
box selection, as we have seen so far.  Once a lasso selection of data points is made 
in the figure above, you can choose "Use Manual Selection" from the `Edit Selection...`
menu at right, which will create a new `Visualizer` selection from the selected data.
The highlight color changes to signify that this is not an editable rectangular box,
and the selected data will be highlighted in *all* figures linked to this `Visualizer`,
including the histograms above.

In [16]:
viz.splom(
    rows=('expand_capacity','time_savings','net_benefits'), 
    cols='L',
    reset=True
)

FigureWidget({
    'data': [{'mode': 'markers',
              'showlegend': False,
              'type': 'scatter',
              'uid': '1ca4414b-ab3b-4271-a869-7ade8603f2e5',
              'x': [],
              'xaxis': 'x',
              'y': [],
              'yaxis': 'y'},
             {'fill': 'tozeroy',
              'line': {'color': 'rgb(31, 119, 180)'},
              'showlegend': False,
              'type': 'scatter',
              'uid': '8e7cb9c5-2df0-44ea-b631-aeef6f837f4f',
              'x': array([ -6.99827744,  -6.4254991 ,  -5.85272077,  -5.27994243,  -4.70716409,
                           -4.13438576,  -3.56160742,  -2.98882909,  -2.41605075,  -1.84327242,
                           -1.27049408,  -0.69771575,  -0.12493741,   0.44784092,   1.02061926,
                            1.5933976 ,   2.16617593,   2.73895427,   3.3117326 ,   3.88451094,
                            4.45728927,   5.03006761,   5.60284594,   6.17562428,   6.74840261,
                        

In [17]:
viz.hmm(
    rows=('time_savings','net_benefits'), 
    cols='L',
    show_points=100,
    reset=True,
)

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



FigureWidget({
    'data': [{'coloraxis': 'coloraxis2',
              'hoverongaps': False,
              'hovertemplate': ('<b>Expand Amount</b>: %{x:.3s}' ... '>%{meta[1]} unselected</extra>'),
              'meta': array([[(0, 0), (0, 0), (0, 0), ..., (0, 0), (0, 0), (0, 0)],
                             [(66, 144), (14, 102), (3, 97), ..., (0, 23), (0, 24), (0, 25)],
                             [(20, 11), (44, 32), (20, 41), ..., (0, 56), (0, 60), (0, 57)],
                             ...,
                             [(0, 0), (0, 0), (0, 0), ..., (0, 0), (0, 0), (0, 0)],
                             [(0, 0), (0, 0), (0, 0), ..., (0, 0), (0, 1), (0, 0)],
                             [(0, 0), (0, 0), (0, 0), ..., (0, 0), (0, 0), (0, 0)]], dtype=object),
              'showlegend': False,
              'type': 'heatmap',
              'uid': 'e6c479cc-f681-4f8b-bfde-cfe93e41df0f',
              'x': array([ 2.5,  7.5, 12.5, 17.5, 22.5, 27.5, 32.5, 37.5, 42.5, 47.5, 52.5, 57.5,
    

In [18]:
viz.new_selection(
    "time_savings * input_flow > 1000 & cost_of_capacity_expansion < 300",
    name="TimeSaved"
)

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



## Dynamic Feature Scoring

EMAT can score the relative importance of inputs for an experiment being within the selection, either for a typical rectangular selection based on thresholds, or for any arbitrary selection. These scores are recomputed and updated in near-real-time as the thresholds are adjusted.

When the selection includes rectangular thresholds set on both inputs and outputs, the thresholded inputs are automatically excluded from the scoring algorithm.

In [19]:
viz.selection_feature_scores()

FigureWidget({
    'data': [{'marker': {'color': 'rgb(255, 127, 14)'},
              'orientation': 'h',
              'text': [0.040, 0.036, 0.351, 0.027, 0.046, 0.031, 0.032, 0.278,
                       0.075, 0.066, 0.018],
              'textposition': 'outside',
              'texttemplate': '%{text}',
              'type': 'bar',
              'uid': '7cbfc054-fbe0-4852-a37a-2acecfa8c000',
              'x': [0.040435434871308476, 0.03573276813405234, 0.3509419166491254,
                    0.027083372133107405, 0.045866176462150215,
                    0.030516686739162836, 0.03199399239500588, 0.2782887415225028,
                    0.07459192583518369, 0.06627182008418823, 0.018277165174212535],
              'y': [alpha, beta, input_flow, value_of_time, unit_cost_expansion,
                    interest_rate, yield_curve, expand_capacity,
                    amortization_period, debt_type, interest_rate_lock]}],
    'layout': {'height': 242,
               'margin': {'b': 0,

## Using PRIM with the Interactive Explorer

The PRIM tools are available directly within the interactive explorer. Simply 
set a target as shown.

In [20]:
prim = viz.prim(target="net_benefits >= 0")

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



In [21]:
box1 = prim.find_box()

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



The tradeoff selector is directly integrated into the explorer.  In addition
to the information visible by hovering over any point in the tradeoff selector
figure, clicking on that point will create a new selection in the explorer, and
set all of the interactive constraints 
to the bounds given by that particular point.

In [22]:
box1.tradeoff_selector()

FigureWidget({
    'data': [{'hoverinfo': 'text',
              'marker': {'color': array([0, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 3, 3,
                                         3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 5, 5, 5, 5,
                                         5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5, 5], dtype=object),
                         'colorbar': {'tickmode': 'array',
                                      'ticks': 'outside',
                                      'ticktext': [0, 1, 2, 3, 4, 5],
                                      'tickvals': array([0.41666667, 1.25      , 2.08333333, 2.91666667, 3.75      , 4.58333333]),
                                      'title': {'side': 'right', 'text': 'Number of Restricted Dimensions'}},
                         'colorscale': [[0.0, 'rgb(70, 49, 126)'],
                                        [0.16666666666666666, 'rgb(70, 49, 126)'],
                                      

In [23]:
box1.select(20)

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



In [24]:
viz.status()

In [25]:
viz.lever_selectors()

OVERLOAD BINS 20 4 36


Box(children=(VBox(children=(FigureWidget({
    'data': [{'hoverinfo': 'skip',
              'marker': {'color…

We can also use PRIM to explore solutions based only on manipulating the
policy levers, and not the combination of all inputs (levers & uncertainties).

In [26]:
prim_levers = viz.prim('levers', target="Profitable")

In [27]:
prim_levers.tradeoff_selector()

/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



/home/runner/work/tmip-emat/tmip-emat/.venv/lib/python3.10/site-packages/jupyter_client/session.py:721: UserWarning:

Message serialization failed with:
Out of range float values are not JSON compliant
Supporting this message is deprecated in jupyter-client 7, please make sure your message is JSON-compliant



FigureWidget({
    'data': [{'hoverinfo': 'text',
              'marker': {'color': array([0, 1, 2, 2, 2, 2, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3,
                                         3, 3, 3, 3, 3, 3, 3], dtype=object),
                         'colorbar': {'tickmode': 'array',
                                      'ticks': 'outside',
                                      'ticktext': [0, 1, 2, 3],
                                      'tickvals': array([0.375, 1.125, 1.875, 2.625]),
                                      'title': {'side': 'right', 'text': 'Number of Restricted Dimensions'}},
                         'colorscale': [[0.0, 'rgb(64, 67, 135)'], [0.25, 'rgb(64,
                                        67, 135)'], [0.25, 'rgb(41, 120, 142)'],
                                        [0.5, 'rgb(41, 120, 142)'], [0.5, 'rgb(34,
                                        167, 132)'], [0.75, 'rgb(34, 167, 132)'],
                                        [0.75, 'rgb(

In [28]:
viz.parcoords()

FigureWidget({
    'data': [{'dimensions': [{'label': '(X) alpha',
                              'name': 'alpha',
                              'range': [0.09302215709849712, 0.20698516202685716],
                              'values': array([0.15413039, 0.14873148, 0.12402743, ..., 0.12637832, 0.11446655,
                                               0.15726593])},
                             {'label': '(X) beta',
                              'name': 'beta',
                              'range': [3.3602508465026704, 5.639676667944243],
                              'values': array([5.0616479 , 4.08866265, 3.95688397, ..., 3.63498798, 4.25812464,
                                               3.64663838])},
                             {'label': '(X) Input Flow',
                              'name': 'input_flow',
                              'range': [75.1, 154.9],
                              'values': array([112, 145,  80, ..., 119,  83,  80])},
                             {